**Paso 1: Configurar el entorno en Google Colab**
Instalar PySpark: Si aún no está instalado en Google Colab, usa este comando para instalarlo:

In [10]:
!pip install pyspark

Defaulting to user installation because normal site-packages is not writeable


**Importar librerías necesarias:**

In [11]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, col, stddev, countDistinct, max


**Crear la sesión de Spark:**

In [12]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, col, stddev, countDistinct, max


**Cargar el archivo CSV en un DataFrame de PySpark:** Primero, debes cargar el archivo air_traffic_data.csv.

In [13]:
# Create a SparkSession
spark = SparkSession.builder.appName("AirTrafficAnalysis").getOrCreate()

# Ruta al archivo en Google Drive
file_path = 'air_traffic_data.csv'

# Cargar los datos en un DataFrame de PySpark
df = spark.read.csv(file_path, header=True, inferSchema=True)
df.show(5)  # Mostrar las primeras filas para verificar la carga


+---------------+-----------------+---------------------------+-----------------+---------------------------+-------------+----------+------------------+-------------------+----------+-------------+---------------+---------------------------+------------------------+----+-----+
|Activity Period|Operating Airline|Operating Airline IATA Code|Published Airline|Published Airline IATA Code|  GEO Summary|GEO Region|Activity Type Code|Price Category Code|  Terminal|Boarding Area|Passenger Count|Adjusted Activity Type Code|Adjusted Passenger Count|Year|Month|
+---------------+-----------------+---------------------------+-----------------+---------------------------+-------------+----------+------------------+-------------------+----------+-------------+---------------+---------------------------+------------------------+----+-----+
|         200507|     ATA Airlines|                         TZ|     ATA Airlines|                         TZ|     Domestic|        US|          Deplaned|          

**Paso 2: Análisis de los datos**
1. Conocer el tipo de datos de cada columna

Para ver los tipos de datos de cada columna y estructurar el DataFrame según se requiere en la primera tarea:

In [14]:

df.printSchema()

company_count = df.select(countDistinct("Operating Airline")).alias("Total de Compañías")
company_count.show()

avg_passengers = df.groupBy("Operating Airline").agg(avg("Passenger Count").alias("Promedio de Pasajeros"))
avg_passengers.show()


root
 |-- Activity Period: integer (nullable = true)
 |-- Operating Airline: string (nullable = true)
 |-- Operating Airline IATA Code: string (nullable = true)
 |-- Published Airline: string (nullable = true)
 |-- Published Airline IATA Code: string (nullable = true)
 |-- GEO Summary: string (nullable = true)
 |-- GEO Region: string (nullable = true)
 |-- Activity Type Code: string (nullable = true)
 |-- Price Category Code: string (nullable = true)
 |-- Terminal: string (nullable = true)
 |-- Boarding Area: string (nullable = true)
 |-- Passenger Count: integer (nullable = true)
 |-- Adjusted Activity Type Code: string (nullable = true)
 |-- Adjusted Passenger Count: integer (nullable = true)
 |-- Year: integer (nullable = true)
 |-- Month: string (nullable = true)

+---------------------------------+
|count(DISTINCT Operating Airline)|
+---------------------------------+
|                               77|
+---------------------------------+



+--------------------+---------------------+
|   Operating Airline|Promedio de Pasajeros|
+--------------------+---------------------+
|          Icelandair|               2799.7|
|         Ameriflight|                  5.0|
|      Cathay Pacific|   17121.325581395347|
|          Aeromexico|    5463.822222222222|
|      Etihad Airways|    6476.088235294118|
| Philippine Airlines|   10248.635658914729|
|United Airlines -...|    48915.46750232126|
|    Turkish Airlines|    8162.416666666667|
| Swiss International|    6061.640287769784|
|    Independence Air|               6391.3|
|Miami Air Interna...|              107.375|
|          Air France|   11589.077519379845|
|      Japan Airlines|    6470.332046332046|
|    Midwest Airlines|               3883.0|
|      Atlas Air, Inc|                 34.0|
|    JetBlue Airways |    35261.13963963964|
|       China Eastern|    5498.402777777777|
|   Mexicana Airlines|    7993.806451612903|
|         Air Canada |   18251.560109289618|
|       Al

**Paso 3: Resolver las preguntas de análisis**
2. Contar el número de compañías diferentes

Para saber cuántas compañías aparecen en el archivo:

In [6]:
company_count = df.select(countDistinct("Operating Airline")).alias("Total de Compañías")
company_count.show()


+---------------------------------+
|count(DISTINCT Operating Airline)|
+---------------------------------+
|                               77|
+---------------------------------+



**3. Calcular el promedio de pasajeros por compañía**

Para calcular el número promedio de pasajeros por cada compañía:

In [63]:
avg_passengers = df.groupBy("Operating Airline").agg(avg("Passenger Count").alias("Promedio de Pasajeros"))
avg_passengers.show()


+--------------------+---------------------+
|   Operating Airline|Promedio de Pasajeros|
+--------------------+---------------------+
|          Icelandair|               2799.7|
|         Ameriflight|                  5.0|
|      Cathay Pacific|   17121.325581395347|
|          Aeromexico|    5463.822222222222|
|      Etihad Airways|    6476.088235294118|
| Philippine Airlines|   10248.635658914729|
|United Airlines -...|    48915.46750232126|
|    Turkish Airlines|    8162.416666666667|
| Swiss International|    6061.640287769784|
|    Independence Air|               6391.3|
|Miami Air Interna...|              107.375|
|          Air France|   11589.077519379845|
|      Japan Airlines|    6470.332046332046|
|    Midwest Airlines|               3883.0|
|      Atlas Air, Inc|                 34.0|
|    JetBlue Airways |    35261.13963963964|
|       China Eastern|    5498.402777777777|
|   Mexicana Airlines|    7993.806451612903|
|         Air Canada |   18251.560109289618|
|       Al

**4. Eliminar duplicados por "GEO Región"**

Para eliminar duplicados en la columna GEO Region, manteniendo solo el registro con el mayor número de pasajeros:

In [19]:
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number

# Crear una ventana de datos por GEO Region
window = Window.partitionBy("GEO Region").orderBy(col("Passenger Count").desc())

# Agregar una columna de número de fila para mantener solo el registro con el mayor número de pasajeros
df_filtered = df.withColumn("row_num", row_number().over(window)).filter(col("row_num") == 1).drop("row_num")
df_filtered.show()


+---------------+--------------------+---------------------------+--------------------+---------------------------+-------------+-------------------+------------------+-------------------+-------------+-------------+---------------+---------------------------+------------------------+----+-------+
|Activity Period|   Operating Airline|Operating Airline IATA Code|   Published Airline|Published Airline IATA Code|  GEO Summary|         GEO Region|Activity Type Code|Price Category Code|     Terminal|Boarding Area|Passenger Count|Adjusted Activity Type Code|Adjusted Passenger Count|Year|  Month|
+---------------+--------------------+---------------------------+--------------------+---------------------------+-------------+-------------------+------------------+-------------------+-------------+-------------+---------------+---------------------------+------------------------+----+-------+
|         200708|United Airlines -...|                         UA|United Airlines -...|                

**5. Exportar resultados a CSV**

Exportar el DataFrame resultante a un archivo CSV:

In [20]:
avg_passengers.coalesce(1).write.csv("average_passengers_per_company.csv", header=True)
df_filtered.coalesce(1).write.csv("filtered_geo_region.csv", header=True)


**Paso 4: Análisis descriptivo y correlación**

**1. Calcular la media y desviación estándar**

Para obtener la media y desviación estándar de las columnas numéricas:

In [22]:
from pyspark.sql.types import IntegerType, FloatType, DoubleType

numeric_columns = [field.name for field in df.schema.fields if field.dataType in [IntegerType(), FloatType(), DoubleType()]]
descriptive_stats = df.select([avg(col).alias(f"{col}_mean") for col in numeric_columns])
descriptive_stats.show()

std_dev_stats = df.select([stddev(col).alias(f"{col}_stddev") for col in numeric_columns])
std_dev_stats.show()

+--------------------+--------------------+-----------------------------+-----------------+
|Activity Period_mean|Passenger Count_mean|Adjusted Passenger Count_mean|        Year_mean|
+--------------------+--------------------+-----------------------------+-----------------+
|  201045.07336576266|  29240.521090157927|           29331.917105350836|2010.385220230559|
+--------------------+--------------------+-----------------------------+-----------------+

+----------------------+----------------------+-------------------------------+-----------------+
|Activity Period_stddev|Passenger Count_stddev|Adjusted Passenger Count_stddev|      Year_stddev|
+----------------------+----------------------+-------------------------------+-----------------+
|    313.33619609986414|    58319.509284123524|               58284.1822186625|3.137589043169972|
+----------------------+----------------------+-------------------------------+-----------------+



**2. Matriz de correlación**

Para calcular una matriz de correlación de las columnas, primero asegúrate de que los tipos de datos sean correctos. Luego, puedes utilizar las funciones de PySpark para calcular la correlación entre cada par de columnas y generar una tabla con los 10 valores más importantes.

In [23]:
# Cambia las columnas de tipo string a tipo double para calcular la correlación
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

numeric_columns = [col for col, dtype in df.dtypes if dtype in ['int', 'double']]
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=numeric_columns, outputCol=vector_col)
df_vector = assembler.transform(df).select(vector_col)

# Calcular la correlación
matrix = Correlation.corr(df_vector, vector_col)
matrix.show()


24/11/02 10:31:56 WARN InstanceBuilder: Failed to load implementation from:dev.ludovic.netlib.blas.JNIBLAS


+----------------------+
|pearson(corr_features)|
+----------------------+
|  1.0              ...|
+----------------------+



In [ ]:
# Instalar la librería de Cassandra para Python
pip install cassandra-driver

In [29]:
# Importo las librerías necesarias
from cassandra.cluster import Cluster
import uuid

# Conectar al clúster de Cassandra
cluster = Cluster(['127.0.0.1'])  # Usa '127.0.0.1' si estás ejecutando Cassandra localmente
session = cluster.connect()

# Crear el keyspace si no existe
session.execute("""
    CREATE KEYSPACE IF NOT EXISTS air_traffic
    WITH REPLICATION = { 'class': 'SimpleStrategy', 'replication_factor': 1 }
""")

# Seleccionar el keyspace
session.set_keyspace('air_traffic')

# Crear la tabla de Aerolíneas
session.execute("""
    CREATE TABLE IF NOT EXISTS airlines (
        airline_id UUID PRIMARY KEY,
        operating_airline TEXT,
        iata_code TEXT,
        passenger_count FLOAT,
        adjusted_passenger_count FLOAT
    );
""")

# Crear la tabla de Destinos y Región Geográfica
session.execute("""
    CREATE TABLE IF NOT EXISTS geo_region (
        region_id UUID PRIMARY KEY,
        geo_summary TEXT,
        geo_region TEXT,
        terminal TEXT,
        boarding_area TEXT
    );
""")

# Crear la tabla de Período de Actividad
session.execute("""
    CREATE TABLE IF NOT EXISTS activity_period (
        period_id UUID PRIMARY KEY,
        activity_period INT,
        year INT,
        month TEXT,
        activity_type_code TEXT
    );
""")

# Insertar datos de ejemplo en las tablas

# Insertar datos en la tabla airlines
airline_id = uuid.uuid4()
session.execute("""
    INSERT INTO airlines (airline_id, operating_airline, iata_code, passenger_count, adjusted_passenger_count)
    VALUES (%s, %s, %s, %s, %s)
""", (airline_id, 'United Airlines', 'UA', 50000, 49000))

# Insertar datos en la tabla geo_region
region_id = uuid.uuid4()
session.execute("""
    INSERT INTO geo_region (region_id, geo_summary, geo_region, terminal, boarding_area)
    VALUES (%s, %s, %s, %s, %s)
""", (region_id, 'North America', 'West Coast', 'Terminal 1', 'Boarding Area A'))

# Insertar datos en la tabla activity_period
period_id = uuid.uuid4()
session.execute("""
    INSERT INTO activity_period (period_id, activity_period, year, month, activity_type_code)
    VALUES (%s, %s, %s, %s, %s)
""", (period_id, 202310, 2023, 'October', 'Departure'))

# Consultar datos de ejemplo de las tablas
print("Datos de la tabla airlines:")
rows = session.execute("SELECT * FROM airlines")
for row in rows:
    print(row)

print("\nDatos de la tabla geo_region:")
rows = session.execute("SELECT * FROM geo_region")
for row in rows:
    print(row)

print("\nDatos de la tabla activity_period:")
rows = session.execute("SELECT * FROM activity_period")
for row in rows:
    print(row)


Datos de la tabla airlines:
Row(airline_id=UUID('aede7d39-1eab-490f-8371-dbe90ab7f1df'), adjusted_passenger_count=49000.0, iata_code='UA', operating_airline='United Airlines', passenger_count=50000.0)
Row(airline_id=UUID('62cd48ee-d7d1-4344-b86e-fb30f86397bc'), adjusted_passenger_count=49000.0, iata_code='UA', operating_airline='United Airlines', passenger_count=50000.0)
Row(airline_id=UUID('285030fc-8471-47db-b3fa-1805fedf879a'), adjusted_passenger_count=49000.0, iata_code='UA', operating_airline='United Airlines', passenger_count=50000.0)
Row(airline_id=UUID('af3534ce-2c8c-42c6-886c-a7ac70b05dc2'), adjusted_passenger_count=49000.0, iata_code='UA', operating_airline='United Airlines', passenger_count=50000.0)
Row(airline_id=UUID('d7982f84-8b11-48d4-bdf5-04da712e7f8d'), adjusted_passenger_count=49000.0, iata_code='UA', operating_airline='United Airlines', passenger_count=50000.0)

Datos de la tabla geo_region:
Row(region_id=UUID('c49d69fa-9856-4d7a-a0ba-bb0d3193948e'), boarding_area='B

In [30]:
# Importar las librerías necesarias adicionales para análisis avanzado
from pyspark.sql import functions as F
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation
from pyspark.ml.clustering import KMeans

# Paso 1: Análisis Avanzado de Correlación
# Crear un vector de características a partir de las columnas numéricas
numeric_columns = ["Passenger Count", "Adjusted Passenger Count", "Activity Period"]
assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features")
df_vector = assembler.transform(df_filtered).select("features")

# Calcular la matriz de correlación
correlation_matrix = Correlation.corr(df_vector, "features").head()[0].toArray()
print("Matriz de Correlación:")
print(correlation_matrix)

# Paso 2: Modelado Predictivo con KMeans
# Configurar y entrenar un modelo KMeans
kmeans = KMeans(featuresCol="features", k=3)
model = kmeans.fit(df_vector)

# Mostrar los centros de los clústeres
centers = model.clusterCenters()
print("Centros de Clústeres: ", centers)

# Paso 3: Exportar Datos Procesados (opcional)
# Exportar el DataFrame a un archivo CSV para su uso posterior en visualización
df_filtered.coalesce(1).write.csv("processed_air_traffic_data.csv", header=True)


Matriz de Correlación:
[[1.         1.         0.00741701]
 [1.         1.         0.00741701]
 [0.00741701 0.00741701 1.        ]]


Centros de Clústeres:  [array([ 22505.28571429,  22505.28571429, 201305.85714286]), array([659837., 659837., 201308.]), array([ 86398.,  86398., 200708.])]


In [ ]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

# Crear un vector de características a partir de las columnas numéricas
numeric_columns = ["Passenger Count", "Adjusted Passenger Count", "Activity Period"]
assembler = VectorAssembler(inputCols=numeric_columns, outputCol="features")
df_vector = assembler.transform(df_filtered).select("features")

# Calcular la matriz de correlación
correlation_matrix = Correlation.corr(df_vector, "features").head()[0].toArray()
print("Matriz de Correlación:")
print(correlation_matrix)

In [31]:
from pyspark.ml.clustering import KMeans

# Configurar y entrenar un modelo KMeans
kmeans = KMeans(featuresCol="features", k=3)
model = kmeans.fit(df_vector)

# Mostrar los centros de los clústeres
centers = model.clusterCenters()
print("Centros de Clústeres: ", centers)


Centros de Clústeres:  [array([ 22505.28571429,  22505.28571429, 201305.85714286]), array([659837., 659837., 201308.]), array([ 86398.,  86398., 200708.])]


In [33]:
# Exportar el DataFrame a un archivo CSV
df_filtered.coalesce(1).write.csv("processed_air_traffic_data.csv", header=True)


**Paso 5: Selección de Algoritmo y Aplicación**

Selecciona un algoritmo como KMeans o LinearRegression dependiendo de los datos y aplica el modelo.

A continuación te muestro un ejemplo de KMeans:

In [ ]:
from pyspark.ml.clustering import KMeans

# Definir el modelo
kmeans = KMeans(featuresCol=vector_col, k=3)
model = kmeans.fit(df_vector)

# Resultados
centers = model.clusterCenters()
print("Centros de Clústeres: ", centers)


Centros de Clústeres:  [array([201037.64852625,  11773.63893153,  11878.91832975,   2010.31117593]), array([201104.95379538, 352369.67656766, 352369.67656766,   2010.98349835]), array([201091.96300716, 106597.56563246, 106597.56563246,   2010.8526253 ])]


Análisis Descriptivo y Conclusiones:

**1. Medias y Desviaciones Estándar**

La media de cada columna proporciona una visión general del "centro" de los datos en cada variable numérica, mientras que la desviación estándar muestra la variabilidad o dispersión en torno a la media. Las variables con alta desviación estándar sugieren mayor variabilidad en los datos.


---



*Conclusión: Si encontramos una desviación estándar significativa en variables
como el "Passenger Count" o "Flight Count," esto puede indicar fluctuaciones en el tráfico de pasajeros o vuelos que podrían depender de factores estacionales o de eventos especiales en el aeropuerto de San Francisco. Esto sugiere que podríamos analizar estas variaciones para ajustar operaciones de vuelos o recursos en el aeropuerto.*



---







**2. Matriz de Correlación**
La matriz de correlación entre variables numéricas ayuda a identificar relaciones directas o inversas entre pares de variables. Valores cercanos a ±1 indican una relación fuerte, mientras que valores cercanos a 0 indican poca o ninguna relación.


---



*Conclusión: Si la matriz de correlación muestra que el "Passenger Count" tiene una correlación positiva fuerte con variables como "Flight Count," podemos inferir que un aumento en la cantidad de vuelos está directamente relacionado con un mayor número de pasajeros. Esto es intuitivo, pero cuantificarlo permite tomar decisiones basadas en datos, como aumentar los recursos de procesamiento de pasajeros cuando se incrementan los vuelos.
Además, si encontramos una correlación negativa entre variables como "Delay Time" y "Flight Count," esto podría indicar que los vuelos más llenos tienden a tener menos demoras, quizás porque se priorizan. Esto puede llevar a decisiones operativas para minimizar demoras en vuelos de alta demanda.*



---



**3. Análisis Temporal (Series Temporales)**
Basado en los principios de series temporales de la **sesión 27**, es posible explorar patrones estacionales o tendencias de largo plazo en variables como el número de pasajeros y vuelos. La descomposición de una serie temporal en sus componentes (tendencia, estacionalidad, y residuo) puede revelar variaciones periódicas.


---



*Conclusión: Si los datos muestran estacionalidad, como picos en el tráfico de pasajeros en ciertos meses o días de la semana, esto podría indicar periodos de alta demanda que puede usar para planificar estrategias de oferta y promoción. Además, si la tendencia es creciente en la cantidad de vuelos y pasajeros, esto podría motivar inversiones en infraestructura o personal adicional.
El análisis de series temporales también podría identificar patrones de demanda en temporadas de vacaciones o eventos locales que afecten el tráfico. Por ejemplo,  podría anticipar la demanda y ajustar sus ofertas para destinos específicos.*


---



**4. Interpretación Subjetiva y Recomendaciones**

A partir de estos análisis cuantitativos, surgen algunas recomendaciones para

*Planificación de Recursos: Basándose en el número promedio de pasajeros y su variabilidad, la empresa podría optimizar los recursos para las temporadas altas y bajas, mejorando la satisfacción del cliente y minimizando costos operativos.*

*Estrategias de Marketing: Con patrones de estacionalidad identificados, puede coordinar campañas promocionales en los meses de mayor tráfico, lo que maximizaría la visibilidad y efectividad de las ofertas.*

*Manejo de Demoras: Si existe una correlación entre el conteo de vuelos y las demoras, podría usar estos datos para mejorar la puntualidad, identificando vuelos de alta prioridad y ajustando horarios operativos.*

**Paso 4: Análisis Descriptivo**

Calcular la Media y Desviación Estándar

A partir de tu DataFrame df, extraemos las columnas numéricas para calcular la media y la desviación estándar. Esto proporciona información clave sobre la centralidad y la dispersión de los datos, como el "Passenger Count".

In [ ]:
from pyspark.sql.types import IntegerType, FloatType, DoubleType

In [ ]:
# Import necessary data types
from pyspark.sql.types import IntegerType, FloatType, DoubleType

# Seleccionar columnas numéricas
numeric_columns = [field.name for field in df.schema.fields if field.dataType in [IntegerType(), FloatType(), DoubleType()]]

# Calcular media
descriptive_stats = df.select([avg(col).alias(f"{col}_mean") for col in numeric_columns])
print("Media de cada columna numérica:")
descriptive_stats.show()

# Calcular desviación estándar
std_dev_stats = df.select([stddev(col).alias(f"{col}_stddev") for col in numeric_columns])
print("Desviación estándar de cada columna numérica:")
std_dev_stats.show()


Media de cada columna numérica:
+--------------------+--------------------+-----------------------------+-----------------+
|Activity Period_mean|Passenger Count_mean|Adjusted Passenger Count_mean|        Year_mean|
+--------------------+--------------------+-----------------------------+-----------------+
|  201045.07336576266|  29240.521090157927|           29331.917105350836|2010.385220230559|
+--------------------+--------------------+-----------------------------+-----------------+

Desviación estándar de cada columna numérica:
+----------------------+----------------------+-------------------------------+-----------------+
|Activity Period_stddev|Passenger Count_stddev|Adjusted Passenger Count_stddev|      Year_stddev|
+----------------------+----------------------+-------------------------------+-----------------+
|    313.33619609986414|    58319.509284123524|               58284.1822186625|3.137589043169972|
+----------------------+----------------------+----------------------

**Conclusión del Análisis Descriptivo:**

La media nos ofrece el promedio de pasajeros y vuelos, lo cual puede ser útil para establecer expectativas básicas de volumen.

La desviación estándar elevada en el conteo de pasajeros o vuelos sugiere fluctuaciones significativas, que podrían implicar estacionalidad o eventos específicos de alto tráfico.

**Paso 5: Matriz de Correlación**

Para obtener una matriz de correlación que permita identificar relaciones entre variables numéricas, debemos transformar estas columnas en un vector.

Transformar las columnas numéricas a un vector: Esto es necesario para utilizar la función de correlación en PySpark.

In [ ]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation

# Crear el vector de características para correlación
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=numeric_columns, outputCol=vector_col)
df_vector = assembler.transform(df).select(vector_col)


Calcular la Matriz de Correlación: Utiliza el método Correlation.corr para calcular la correlación de Pearson entre las columnas numéricas.

In [ ]:
# Calcular la matriz de correlación
correlation_matrix = Correlation.corr(df_vector, vector_col).head()[0].toArray()
print("Matriz de Correlación:")
print(correlation_matrix)


Matriz de Correlación:
[[1.         0.06031063 0.05933631 0.99993987]
 [0.06031063 1.         0.99994089 0.06006904]
 [0.05933631 0.99994089 1.         0.05909623]
 [0.99993987 0.06006904 0.05909623 1.        ]]


**Conclusión de la Matriz de Correlación:**

Una correlación alta entre "Passenger Count" y "Flight Count" (o variables relacionadas) indicaría una relación directa entre el número de vuelos y el número de pasajeros.

Una correlación negativa entre variables como "Delay Time" y "Flight Count" podría sugerir que los vuelos de alta prioridad tienden a tener menos demoras, indicando posibles oportunidades de optimización para minimizar demoras en vuelos críticos.

**Paso 6: Selección y Aplicación de Algoritmo**

Si deseas agrupar los datos para análisis adicionales, puedes aplicar un algoritmo de clustering como K-Means para observar patrones. A continuación, se muestra un ejemplo de K-Means con k=3 clústeres.

Aplicar K-Means:

In [ ]:
from pyspark.ml.clustering import KMeans

# Configurar y entrenar el modelo KMeans
kmeans = KMeans(featuresCol=vector_col, k=3)
model = kmeans.fit(df_vector)

# Obtener los centros de los clústeres
centers = model.clusterCenters()
print("Centros de Clústeres: ", centers)


Centros de Clústeres:  [array([201037.64852625,  11773.63893153,  11878.91832975,   2010.31117593]), array([201104.95379538, 352369.67656766, 352369.67656766,   2010.98349835]), array([201091.96300716, 106597.56563246, 106597.56563246,   2010.8526253 ])]


**Conclusión del Clustering:**

Los centros de los clústeres ofrecen insight sobre grupos naturales en los datos, lo cual puede ser útil para segmentar pasajeros o vuelos basados en patrones de comportamiento.
Puedes identificar periodos de alto y bajo tráfico y ajustar recursos y servicios para mejorar la eficiencia operativa.

**Para visualizar el análisis descriptivo y la matriz de correlación de tus datos de tráfico aéreo usando Plotly,** te proporciono el código paso a paso. Esto incluirá gráficos interactivos para analizar las medias y desviaciones estándar, además de una matriz de correlación.

**Paso 1: Configurar e importar librerías necesarias**
Primero, instala e importa las librerías requeridas.

In [ ]:
# Instalar plotly
!pip install plotly

# Importar las librerías necesarias
import plotly.graph_objects as go
import plotly.express as px
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, stddev, col
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation


**Paso 2: Cargar datos y configurar la sesión de Spark**

In [ ]:
# Crear una sesión de Spark
spark = SparkSession.builder.appName("AirTrafficAnalysis").getOrCreate()

# Ruta al archivo en Google Drive
file_path = 'air_traffic_data.csv'

# Cargar los datos en un DataFrame de PySpark
df = spark.read.csv(file_path, header=True, inferSchema=True)
df.show(5)


+---------------+-----------------+---------------------------+-----------------+---------------------------+-------------+----------+------------------+-------------------+----------+-------------+---------------+---------------------------+------------------------+----+-----+
|Activity Period|Operating Airline|Operating Airline IATA Code|Published Airline|Published Airline IATA Code|  GEO Summary|GEO Region|Activity Type Code|Price Category Code|  Terminal|Boarding Area|Passenger Count|Adjusted Activity Type Code|Adjusted Passenger Count|Year|Month|
+---------------+-----------------+---------------------------+-----------------+---------------------------+-------------+----------+------------------+-------------------+----------+-------------+---------------+---------------------------+------------------------+----+-----+
|         200507|     ATA Airlines|                         TZ|     ATA Airlines|                         TZ|     Domestic|        US|          Deplaned|          

**Paso 3: Calcular la Media y Desviación Estándar**
A continuación, calculamos la media y desviación estándar de las columnas numéricas.

In [ ]:
# Seleccionar columnas numéricas
numeric_columns = [field.name for field in df.schema.fields if field.dataType in ["int", "double"]]

# Calcular media y desviación estándar
mean_values = df.select([avg(col).alias(f"{col}_mean") for col in numeric_columns])
std_dev_values = df.select([stddev(col).alias(f"{col}_stddev") for col in numeric_columns])

# Convertir resultados a Pandas para visualizar con Plotly
mean_df = mean_values.toPandas()
std_dev_df = std_dev_values.toPandas()


**Paso 4: Visualización de Media y Desviación Estándar con Plotly**
Usamos Plotly para crear gráficos de barras para comparar las medias y desviaciones estándar de cada variable numérica.

Media de cada columna numérica:

In [ ]:
fig_mean = px.bar(mean_df.melt(var_name="Variables", value_name="Media"),
                  x="Variables", y="Media", title="Media de cada columna numérica")
fig_mean.update_layout({
    'plot_bgcolor': 'rgba(0, 0, 0, 0)',
    'paper_bgcolor': 'rgba(0, 0, 0, 0)',
    'xaxis_title': 'Variables',
    'yaxis_title': 'Media'
})
fig_mean.show()


Desviación Estándar de cada columna numérica:

In [ ]:
fig_stddev = px.bar(std_dev_df.melt(var_name="Variables", value_name="Desviación Estándar"),
                    x="Variables", y="Desviación Estándar", title="Desviación Estándar de cada columna numérica")
fig_stddev.update_layout({
    'plot_bgcolor': 'rgba(0, 0, 0, 0)',
    'paper_bgcolor': 'rgba(0, 0, 0, 0)',
    'xaxis_title': 'Variables',
    'yaxis_title': 'Desviación Estándar'
})
fig_stddev.show()


**Paso 5: Matriz de Correlación con Plotly**
Transformar las columnas numéricas a un vector y calcular la matriz de correlación.

In [ ]:
# Crear el vector de características para la matriz de correlación
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=numeric_columns, outputCol=vector_col)
df_vector = assembler.transform(df).select(vector_col)

# Calcular la matriz de correlación
correlation_matrix = Correlation.corr(df_vector, vector_col).head()[0].toArray()


Py4JJavaError: An error occurred while calling z:org.apache.spark.ml.stat.Correlation.corr.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 239.0 failed 1 times, most recent failure: Lost task 0.0 in stage 239.0 (TID 211) (1dc6d2bd4eab executor driver): java.lang.IllegalArgumentException: requirement failed: Vector should have dimension larger than zero.
	at scala.Predef$.require(Predef.scala:281)
	at org.apache.spark.ml.stat.SummarizerBuffer.add(Summarizer.scala:476)
	at org.apache.spark.mllib.stat.Statistics$.$anonfun$colStats$1(Statistics.scala:59)
	at scala.collection.TraversableOnce$folder$1.apply(TraversableOnce.scala:196)
	at scala.collection.TraversableOnce$folder$1.apply(TraversableOnce.scala:194)
	at scala.collection.Iterator.foreach(Iterator.scala:943)
	at scala.collection.Iterator.foreach$(Iterator.scala:943)
	at scala.collection.AbstractIterator.foreach(Iterator.scala:1431)
	at scala.collection.TraversableOnce.foldLeft(TraversableOnce.s

In [ ]:
from pyspark.ml.feature import Imputer
from pyspark.sql.types import IntegerType, FloatType, DoubleType

# Select only numeric columns
numeric_columns = [
    field.name
    for field in df.schema.fields
    if field.dataType in [IntegerType(), FloatType(), DoubleType()]
]

# Create and fit the Imputer
imputer = Imputer(
    inputCols=numeric_columns, outputCols=[f"{c}_imputed" for c in numeric_columns]
)
df_imputed = imputer.fit(df).transform(df)

# Update numeric_columns with imputed columns
numeric_columns = [f"{c}_imputed" for c in numeric_columns]

# Recreate the vector assembler with imputed columns
vector_col = "corr_features"
assembler = VectorAssembler(inputCols=numeric_columns, outputCol=vector_col)
df_vector = assembler.transform(df_imputed).select(vector_col)

# Calculate the correlation matrix
correlation_matrix = Correlation.corr(df_vector, vector_col).head()[0].toArray()

# Display the correlation matrix (optional)
print(correlation_matrix)

[[1.         0.06031063 0.05933631 0.99993987]
 [0.06031063 1.         0.99994089 0.06006904]
 [0.05933631 0.99994089 1.         0.05909623]
 [0.99993987 0.06006904 0.05909623 1.        ]]


In [ ]:
df_no_missing = df_imputed.dropna(subset=numeric_columns)

In [ ]:
# Recreate the vector assembler with imputed or non-missing columns
assembler = VectorAssembler(inputCols=numeric_columns, outputCol=vector_col)
df_vector = assembler.transform(df_imputed).select(vector_col) # Use df_imputed or df_no_missing

# Calculate the correlation matrix
correlation_matrix = Correlation.corr(df_vector, vector_col).head()[0].toArray()

In [ ]:
# If not already installed, install Plotly
!pip install plotly

# Import Plotly
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
from pyspark.sql import SparkSession
from pyspark.sql.functions import avg, stddev, col
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.stat import Correlation


In [ ]:
# Initialize Spark session
spark = SparkSession.builder.appName("AirTrafficAnalysis").getOrCreate()

# Load the dataset from your file
file_path = 'air_traffic_data.csv'
df = spark.read.csv(file_path, header=True, inferSchema=True)


In [ ]:
monthly_passenger_counts = df.groupBy("Year", "Month", "Operating Airline").agg(
    avg("Passenger Count").alias("Average Passenger Count")
).toPandas()


In [ ]:
fig_line = px.line(
    monthly_passenger_counts,
    x="Year", y="Average Passenger Count",
    color="Operating Airline",
    title="Average Passenger Count Over Time by Airline"
)

# Adding dropdown menu to select airline
airlines = monthly_passenger_counts["Operating Airline"].unique()
fig_line.update_layout(
    updatemenus=[{
        'buttons': [
            {'label': 'All', 'method': 'update', 'args': [{'visible': [True] * len(airlines)}, {'title': 'All Airlines'}]},
            *[
                {'label': airline, 'method': 'update', 'args': [{'visible': [a == airline for a in airlines]}, {'title': airline}]}
                for airline in airlines
            ]
        ],
        'direction': 'down',
        'showactive': True,
    }]
)
fig_line.show()


In [ ]:
# Convert correlation matrix to Pandas DataFrame
correlation_matrix = Correlation.corr(df_vector, vector_col).head()[0].toArray()
correlation_df = pd.DataFrame(correlation_matrix, columns=numeric_columns, index=numeric_columns)

# Create an interactive heatmap with hover for correlation values
fig_heatmap = go.Figure(
    data=go.Heatmap(
        z=correlation_df.values,
        x=correlation_df.columns,
        y=correlation_df.index,
        colorscale="Viridis",
        hoverongaps=False,
        text=[[f"{val:.2f}" for val in row] for row in correlation_df.values],
        hoverinfo="text"
    )
)
fig_heatmap.update_layout(
    title="Interactive Correlation Heatmap",
    xaxis_title="Variables",
    yaxis_title="Variables",
    plot_bgcolor='rgba(0, 0, 0, 0)',
    paper_bgcolor='rgba(0, 0, 0, 0)'
)
fig_heatmap.show()


In [ ]:
# Prepare data for the scatter matrix
# Assuming you stored the original numeric columns as original_numeric_columns
scatter_data = df.select(original_numeric_columns).toPandas()

# Create a scatter matrix
fig_matrix = px.scatter_matrix(
    scatter_data,
    dimensions=numeric_columns,
    title="Scatter Matrix of Numeric Variables",
    color_discrete_sequence=px.colors.qualitative.Plotly
)

fig_matrix.update_layout(
    dragmode='select',
    width=1000,
    height=1000,
    plot_bgcolor='rgba(0, 0, 0, 0)',
    paper_bgcolor='rgba(0, 0, 0, 0)'
)
fig_matrix.show()


IndentationError: unexpected indent (<ipython-input-87-ff3b811dcfd5>, line 3)

In [ ]:
# Calculate top airlines by average passenger count
top_airlines = monthly_passenger_counts.groupby("Operating Airline")["Average Passenger Count"].mean().nlargest(10).reset_index()

fig_bar = px.bar(
    top_airlines,
    x="Operating Airline",
    y="Average Passenger Count",
    title="Top 10 Airlines by Average Passenger Count",
    text="Average Passenger Count"
)
fig_bar.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig_bar.update_layout(
    xaxis_title="Operating Airline",
    yaxis_title="Average Passenger Count",
    plot_bgcolor='rgba(0, 0, 0, 0)',
    paper_bgcolor='rgba(0, 0, 0, 0)'
)
fig_bar.show()


In [ ]:
# Prepare the data by grouping and calculating monthly averages
monthly_passenger_counts = df.groupBy("Year", "Month", "Operating Airline").agg(
    avg("Passenger Count").alias("Average Passenger Count")
).toPandas()

# Sort data by year and month to ensure correct animation sequence
monthly_passenger_counts = monthly_passenger_counts.sort_values(by=["Year", "Month"])


In [ ]:
import plotly.express as px

# Convert Year and Month to a combined "Date" column for better control
monthly_passenger_counts["Date"] = pd.to_datetime(
    monthly_passenger_counts["Year"].astype(str) + "-" + monthly_passenger_counts["Month"]
)

# Create an animated line chart
fig_animation = px.line(
    monthly_passenger_counts,
    x="Date",
    y="Average Passenger Count",
    color="Operating Airline",
    title="Monthly Average Passenger Count by Airline Over Time",
    animation_frame="Date"  # Frame by each month
)

# Customize the layout for better visibility
fig_animation.update_layout({
    'plot_bgcolor': 'rgba(0, 0, 0, 0)',
    'paper_bgcolor': 'rgba(0, 0, 0, 0)',
    'xaxis_title': 'Date',
    'yaxis_title': 'Average Passenger Count',
})

fig_animation.show()


<ipython-input-90-e5f1416edd73>:4: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



In [ ]:
# Set custom animation settings for play/pause controls
fig_animation.update_layout(
    updatemenus=[dict(
        type="buttons",
        showactive=False,
        buttons=[
            dict(label="Play",
                 method="animate",
                 args=[None, {"frame": {"duration": 500, "redraw": True},
                              "fromcurrent": True, "mode": "immediate"}]),
            dict(label="Pause",
                 method="animate",
                 args=[[None], {"frame": {"duration": 0, "redraw": False},
                                "mode": "immediate", "transition": {"duration": 0}}])
        ]
    )]
)


In [ ]:
# Aggregate to get the top airlines over time
top_airlines = monthly_passenger_counts.groupby("Date").apply(
    lambda x: x.nlargest(5, "Average Passenger Count")
).reset_index(drop=True)

# Create an animated bar chart
fig_bar_animation = px.bar(
    top_airlines,
    x="Operating Airline",
    y="Average Passenger Count",
    color="Operating Airline",
    title="Top 5 Airlines by Average Passenger Count Over Time",
    animation_frame="Date",
    range_y=[0, top_airlines["Average Passenger Count"].max()]  # Set a fixed y-axis range for consistency
)

# Show the figure
fig_bar_animation.show()


<ipython-input-92-574527fa973a>:2: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



In [ ]:
# Prepare data with an additional "Flight Count" column (assuming it's in your dataset)
monthly_data = df.groupBy("Year", "Month", "Operating Airline").agg(
    avg("Passenger Count").alias("Average Passenger Count"),
    avg("Flight Count").alias("Average Flight Count")
).toPandas()

# Sort data for animation
monthly_data["Date"] = pd.to_datetime(monthly_data["Year"].astype(str) + "-" + monthly_data["Month"])
monthly_data = monthly_data.sort_values(by=["Date"])

# Create the animated scatter plot
fig_scatter_animation = px.scatter(
    monthly_data,
    x="Average Flight Count",
    y="Average Passenger Count",
    size="Average Passenger Count",  # Bubble size represents passenger count
    color="Operating Airline",
    title="Passenger Count vs. Flight Count Over Time by Airline",
    animation_frame="Date",
    hover_name="Operating Airline",
    log_x=True,  # Optional: log scale for better visibility
    range_x=[0, monthly_data["Average Flight Count"].max()],
    range_y=[0, monthly_data["Average Passenger Count"].max()]
)

fig_scatter_animation.show()


AnalysisException: [UNRESOLVED_COLUMN.WITH_SUGGESTION] A column or function parameter with name `Flight Count` cannot be resolved. Did you mean one of the following? [`Passenger Count`, `GEO Region`, `Month`, `Activity Period`, `GEO Summary`].;
'Aggregate [Year#2740, Month#2741, Operating Airline#2727], [Year#2740, Month#2741, Operating Airline#2727, avg(Passenger Count#2737) AS Average Passenger Count#2852, avg('Flight Count) AS Average Flight Count#2854]
+- Relation [Activity Period#2726,Operating Airline#2727,Operating Airline IATA Code#2728,Published Airline#2729,Published Airline IATA Code#2730,GEO Summary#2731,GEO Region#2732,Activity Type Code#2733,Price Category Code#2734,Terminal#2735,Boarding Area#2736,Passenger Count#2737,Adjusted Activity Type Code#2738,Adjusted Passenger Count#2739,Year#2740,Month#2741] csv


In [ ]:
# Adjust animation speed
fig_animation.update_layout(
    transition=dict(duration=500),  # Duration of the transition between frames
    frame=dict(duration=1000, redraw=True)  # Duration each frame is displayed
)


ValueError: Invalid property specified for object of type plotly.graph_objs.Layout: 'frame'

Did you mean "dragmode"?

    Valid properties:
        activeselection
            :class:`plotly.graph_objects.layout.Activeselection`
            instance or dict with compatible properties
        activeshape
            :class:`plotly.graph_objects.layout.Activeshape`
            instance or dict with compatible properties
        annotations
            A tuple of
            :class:`plotly.graph_objects.layout.Annotation`
            instances or dicts with compatible properties
        annotationdefaults
            When used in a template (as
            layout.template.layout.annotationdefaults), sets the
            default property values to use for elements of
            layout.annotations
        autosize
            Determines whether or not a layout width or height that
            has been left undefined by the user is initialized on
            each relayout. Note that, regar

In [ ]:
# Prepare data by grouping and calculating monthly average of Passenger Count
monthly_data = df.groupBy("Year", "Month", "Operating Airline").agg(
    avg("Passenger Count").alias("Average Passenger Count")
).toPandas()

# Combine Year and Month into a "Date" column for ordering in animation
monthly_data["Date"] = pd.to_datetime(monthly_data["Year"].astype(str) + "-" + monthly_data["Month"])
monthly_data = monthly_data.sort_values(by=["Date"])


<ipython-input-95-ea00b246e860>:7: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



In [ ]:
import plotly.express as px

# Create the animated scatter plot for Average Passenger Count over time by airline
fig_scatter_animation = px.scatter(
    monthly_data,
    x="Date",
    y="Average Passenger Count",
    size="Average Passenger Count",  # Bubble size represents passenger count
    color="Operating Airline",
    title="Average Passenger Count Over Time by Airline",
    animation_frame="Date",
    hover_name="Operating Airline",
    range_y=[0, monthly_data["Average Passenger Count"].max()]  # Set range for y-axis
)

# Show the animated scatter plot
fig_scatter_animation.show()
